# 임베딩 벡터를 활용한 문제 추천 시스템 구축

1. 개요
- 학습에 있어서(특히 어느 정도 암기와 이해가 필요한 saa-c03같은 경우) 중요한 것 중 하나는 오답 노트 정리.
- 학습을 도와주는 앱으로써, 문제에 대한 기본적인 해설 및 선지에 대한 해설, 단원 분류 등을 제공하고, 추가적으로 해당 문제에 대한 추가학습을 돕기 위해 추천 문제를 제공해주면 좋을 것이라는 판단.
- 즉, 학습의 연속성을 이어가서 효율적으로 틀린 부분, 이해가 부족한 부분을 확실히 하고 넘어갈 수 있도록 문제들을 그룹화시킬 수 있는 방안에 대한 고민

2. 추천 시스템 기본 아이디어
1) 기본적으로 유사한 내용의 문제들이 서로 비슷한 개념을 공유할 것이라는 가정. 또한 해당 문제들은 비슷한 개념들을 조금씩 다르게 표현할 것이기에 이러한 비슷한 개념을 공유하는 문제들을 함께 공부하면 하나의 개념을 다양하게 학습하여 학습에 도움이 될 것이라는 판단.
2) 비슷한 내용의 문제들을 어떻게 찾을 수 있을까?? -> 검색 시스템과 유사.. 임베딩 모델의 발달로 임베딩 모델의 성능을 활용한 벡터 검색을 적용해보자!


3. 임베딩 모델 적용 방법론
1) gpt 임베딩 모델 사용 - (최근에 오픈소스 llm들의 임베딩 모델들이 좋아서 사용해보고 싶엇으나.. gpu가 없음)
2) 기본적인 베이스라인 (유사 문제 추천: 문제 지문 유사 상위 5개 추천, 지문 문제 추천: 지문과 문제 유사 상위 3개 추천)
3) 이후 여러 방법론(키워드 등)을 적용하여 성능 올려보기

## 1. GPT 임베딩을 활용한 문제 추천(베이스라인)

결과물 : 기존 questions_fixed_complete.json에 추천 문제, 및 각 선지별 추천 문제 리스트 필드가 추가된 recommendation_qa_baseline.json

In [2]:
#데이터 불러오기
import json
with open("/Users/twj/Desktop/aws_project/aws_saa_test_backend/data_generate/data_json변환/questions_fixed_complete.json", "r") as f:
    data = json.load(f)

# print(data)


In [9]:
import pandas as pd

selection_list = ["SelectA","SelectB","SelectC","SelectD","SelectE","SelectF","SelectG","SelectH"]
columns = ['index','Domain','Question_Number','Keywords','Terms','division','mapping','Embedding_content']
embedding_list=[]
for i, v in enumerate(data):
    print(v)
    embedding_list.append([i, v['Domain'],v['Question_Number'],v['Keywords'], v['Terms'],'Description','Question_Description',v['Question_Description']])
    for s in selection_list:
        try:
            embedding_list.append([i, v['Domain'],v['Question_Number'],v['Keywords'], v['Terms'],'Selection',s,v[s]])
        except:
            pass

df = pd.DataFrame(embedding_list,columns=columns)
df

{'Question_Number': 'Q1', 'Question_Description': '한 회사가 여러 대륙의 도시들에서 온도, 습도, 대기압 데이터를 수집하고 있습니다. 각 사이트에서 매일 수집하는 평균 데이터 볼륨은 500GB입니다. 각 사이트는 고속 인터넷 연결을 보유하고 있습니다. 회사는 이러한 모든 글로벌 사이트의 데이터를 단일 Amazon S3 버킷에 가능한 한 빠르게 집계하려고 합니다. 솔루션은 운영 복잡성을 최소화해야 합니다. 이러한 요구사항을 충족하는 솔루션은 무엇입니까?', 'Answer': 'A', 'Link': 'https://www.examtopics.com/discussions/amazon/view/84973-exam-aws-certified-solut', 'AnswerDescription': '이 문제는 전 세계 지점에서 발생하는 대규모 데이터를 단일 Amazon S3 버킷으로 빠르고 간편하게 업로드하는 방법을 묻고 있습니다. S3 Transfer Acceleration을 사용하면 네트워크 지연을 줄이고, Multipart Upload로 대용량 데이터를 병렬 전송하여 업로드 속도를 높이는 최적의 해법을 구현할 수 있습니다.', 'Domain': '고성능 아키텍처 설계', 'Tasks': ['3.1', '3.4'], 'Keywords': ['글로벌 사이트', '500GB', '고속 인터넷', '운영 복잡성', 'Amazon S3', 'S3 Transfer Acceleration', 'Multipart Upload'], 'Terms': ['S3 Transfer Acceleration', 'Multipart Upload', 'S3 Cross-Region Replication', 'AWS Snowball Edge', 'Amazon EBS', 'EBS Snapshot'], 'SelectA': '대상 S3 버킷에서 S3 Transfer Acceleration을 활성화하고, Multipart Upload를 사용해 사이트 데이터를 직접 업로드합

index       Domain Question_Number  \
0         0  고성능 아키텍처 설계              Q1   
1         0  고성능 아키텍처 설계              Q1   
2         0  고성능 아키텍처 설계              Q1   
3         0  고성능 아키텍처 설계              Q1   
4         0  고성능 아키텍처 설계              Q1   
...     ...          ...             ...   
5216   1016   보안 아키텍처 설계           Q1019   
5217   1016   보안 아키텍처 설계           Q1019   
5218   1016   보안 아키텍처 설계           Q1019   
5219   1016   보안 아키텍처 설계           Q1019   
5220   1016   보안 아키텍처 설계           Q1019   

                                               Keywords  \
0     [글로벌 사이트, 500GB, 고속 인터넷, 운영 복잡성, Amazon S3, S3...   
1     [글로벌 사이트, 500GB, 고속 인터넷, 운영 복잡성, Amazon S3, S3...   
2     [글로벌 사이트, 500GB, 고속 인터넷, 운영 복잡성, Amazon S3, S3...   
3     [글로벌 사이트, 500GB, 고속 인터넷, 운영 복잡성, Amazon S3, S3...   
4     [글로벌 사이트, 500GB, 고속 인터넷, 운영 복잡성, Amazon S3, S3...   
...                                                 ...   
5216  [Amazon API Gateway, HTTP API, 회사 내부 네트워크, IP ...   
5217  [Amazon API Gateway, HTTP API, 회사 내부 네트워크, IP ...   
5218  [Amazon API Gateway, HTTP API, 회사 내부 네트워크, IP ...   
5219  [Amazon API Gateway, HTTP API, 회사 내부 네트워크, IP ...   
5220  [Amazon API Gateway, HTTP API, 회사 내부 네트워크, IP ...   

                                                  Terms     division  \
0     [S3 Transfer Acceleration, Multipart Upload, S...  Description   
1     [S3 Transfer Acceleration, Multipart Upload, S...    Selection   
2     [S3 Transfer Acceleration, Multipart Upload, S...    Selection   
3     [S3 Transfer Acceleration, Multipart Upload, S...    Selection   
4     [S3 Transfer Acceleration, Multipart Upload, S...    Selection   
...                                                 ...          ...   
5216  [Amazon API Gateway, Resource Policy, Security...  Description   
5217  [Amazon API Gateway, Resource Policy, Security...    Selection   
5218  [Amazon API Gateway, Resource Policy, Security...    Selection   
5219  [Amazon API Gateway, Resource Policy, Security...    Selection   
5220  [Amazon API Gateway, Resource Policy, Security...    Selection   

                   mapping                                  Embedding_content  
0     Question_Description  한 회사가 여러 대륙의 도시들에서 온도, 습도, 대기압 데이터를 수집하고 있습니다....  
1                  SelectA  대상 S3 버킷에서 S3 Transfer Acceleration을 활성화하고, Mu...  
2                  SelectB  가장 가까운 리전의 S3 버킷에 데이터를 업로드하고, S3 Cross-Region ...  
3                  SelectC  AWS Snowball Edge Storage Optimized 디바이스를 매일 예...  
4                  SelectD  가장 가까운 리전의 Amazon EC2 인스턴스에 데이터를 업로드하고, Amazon...  
...                    ...                                                ...  
5216  Question_Description  한 회사가 AWS Cloud에서 애플리케이션을 개발 중입니다. 애플리케이션의 HTT...  
5217               SelectA  API Gateway에 Private Integration을 설정하고 사전에 정의된...  
5218               SelectB  API에 Resource Policy를 생성하여 명시적으로 허용되지 않은 모든 IP...  
5219               SelectC  API를 사설 서브넷에 직접 배포하고, Network ACL을 생성하여 특정 IP ...  
5220               SelectD  API Gateway에 연결된 Security Group을 수정하여 신뢰할 수 있는...  

[5221 rows x 8 columns]

In [7]:
df.iloc[0]['Keywords']

'글로벌 사이트'

In [21]:
from openai import OpenAI
from pydantic import BaseModel
from typing import Dict, List
from dotenv import load_dotenv
import google.generativeai as genai
import os
import json
import ast



load_dotenv()
api_key = os.getenv("GEMINI_API_KEY")
client = OpenAI(api_key=api_key)
genai.configure(api_key=os.environ.get("GOOGLE_API_KEY"))
EMBEDDING_MODEL = "models/embedding-001"
def get_embedding(text):
    if pd.isna(text) or text == "":
        return None  # Handle empty or NaN values gracefully
    try:
        # The API expects a list of contents for embedding
        result = genai.embed_content(model=EMBEDDING_MODEL, content=[str(text)], task_type="retrieval_document")
        return result['embedding'][0] # Extract the embedding vector
    except Exception as e:
        print(f"Error generating embedding for text: '{text}' - {e}")
        return None
    
# --- 전처리 함수 ---
def process_list_string(item):
    # Handle None, or actual NaN values (if they might appear for missing lists)
    if item is None or (isinstance(item, float) and pd.isna(item)):
        return ""
    
    # If it's a list, join its elements
    if isinstance(item, list):
        # Handle empty lists
        if not item: # Checks if the list is empty
            return ""
        # Convert all list elements to string before joining
        return ' '.join(map(str, item))
    
    # If it's not a list, but also not None/NaN, convert to string
    return str(item)
print("Preprocessing 'keywords' column...")
df['Keywords'] = df['Keywords'].apply(process_list_string)

print("Preprocessing 'Terms' column...")
df['Terms'] = df['Terms'].apply(process_list_string)

# --- End of Preprocessing ---
print("Generating embeddings for 'Keywords' column...")
df['keywords_embedding'] = df['Keywords'].apply(get_embedding)

print("Generating embeddings for 'Terms' column...")
df['Terms_embedding'] = df['Terms'].apply(get_embedding)

print("Generating embeddings for 'Embedding_content' column...")
df['Embedding_content_embedding'] = df['Embedding_content'].apply(get_embedding)
df

Preprocessing 'keywords' column...
Preprocessing 'Terms' column...
Generating embeddings for 'keywords' column...
Generating embeddings for 'Terms' column...
Generating embeddings for 'Embedding_content' column...


index       Domain Question_Number  \
0         0  고성능 아키텍처 설계              Q1   
1         0  고성능 아키텍처 설계              Q1   
2         0  고성능 아키텍처 설계              Q1   
3         0  고성능 아키텍처 설계              Q1   
4         0  고성능 아키텍처 설계              Q1   
...     ...          ...             ...   
5216   1016   보안 아키텍처 설계           Q1019   
5217   1016   보안 아키텍처 설계           Q1019   
5218   1016   보안 아키텍처 설계           Q1019   
5219   1016   보안 아키텍처 설계           Q1019   
5220   1016   보안 아키텍처 설계           Q1019   

                                               Keywords  \
0     글로벌 사이트 500GB 고속 인터넷 운영 복잡성 Amazon S3 S3 Trans...   
1     글로벌 사이트 500GB 고속 인터넷 운영 복잡성 Amazon S3 S3 Trans...   
2     글로벌 사이트 500GB 고속 인터넷 운영 복잡성 Amazon S3 S3 Trans...   
3     글로벌 사이트 500GB 고속 인터넷 운영 복잡성 Amazon S3 S3 Trans...   
4     글로벌 사이트 500GB 고속 인터넷 운영 복잡성 Amazon S3 S3 Trans...   
...                                                 ...   
5216  Amazon API Gateway HTTP API 회사 내부 네트워크 IP 주소 제...   
5217  Amazon API Gateway HTTP API 회사 내부 네트워크 IP 주소 제...   
5218  Amazon API Gateway HTTP API 회사 내부 네트워크 IP 주소 제...   
5219  Amazon API Gateway HTTP API 회사 내부 네트워크 IP 주소 제...   
5220  Amazon API Gateway HTTP API 회사 내부 네트워크 IP 주소 제...   

                                                  Terms     division  \
0     S3 Transfer Acceleration Multipart Upload S3 C...  Description   
1     S3 Transfer Acceleration Multipart Upload S3 C...    Selection   
2     S3 Transfer Acceleration Multipart Upload S3 C...    Selection   
3     S3 Transfer Acceleration Multipart Upload S3 C...    Selection   
4     S3 Transfer Acceleration Multipart Upload S3 C...    Selection   
...                                                 ...          ...   
5216  Amazon API Gateway Resource Policy Security Gr...  Description   
5217  Amazon API Gateway Resource Policy Security Gr...    Selection   
5218  Amazon API Gateway Resource Policy Security Gr...    Selection   
5219  Amazon API Gateway Resource Policy Security Gr...    Selection   
5220  Amazon API Gateway Resource Policy Security Gr...    Selection   

                   mapping                                  Embedding_content  \
0     Question_Description  한 회사가 여러 대륙의 도시들에서 온도, 습도, 대기압 데이터를 수집하고 있습니다....   
1                  SelectA  대상 S3 버킷에서 S3 Transfer Acceleration을 활성화하고, Mu...   
2                  SelectB  가장 가까운 리전의 S3 버킷에 데이터를 업로드하고, S3 Cross-Region ...   
3                  SelectC  AWS Snowball Edge Storage Optimized 디바이스를 매일 예...   
4                  SelectD  가장 가까운 리전의 Amazon EC2 인스턴스에 데이터를 업로드하고, Amazon...   
...                    ...                                                ...   
5216  Question_Description  한 회사가 AWS Cloud에서 애플리케이션을 개발 중입니다. 애플리케이션의 HTT...   
5217               SelectA  API Gateway에 Private Integration을 설정하고 사전에 정의된...   
5218               SelectB  API에 Resource Policy를 생성하여 명시적으로 허용되지 않은 모든 IP...   
5219               SelectC  API를 사설 서브넷에 직접 배포하고, Network ACL을 생성하여 특정 IP ...   
5220               SelectD  API Gateway에 연결된 Security Group을 수정하여 신뢰할 수 있는...   

                                     keywords_embedding  \
0     [0.082221694, -0.036399595, -0.054603774, -0.0...   
1     [0.082221694, -0.036399595, -0.054603774, -0.0...   
2     [0.082221694, -0.036399595, -0.054603774, -0.0...   
3     [0.082221694, -0.036399595, -0.054603774, -0.0...   
4     [0.082221694, -0.036399595, -0.054603774, -0.0...   
...                                                 ...   
5216  [0.047030162, -0.03762929, -0.055747997, 0.016...   
5217  [0.047030162, -0.03762929, -0.055747997, 0.016...   
5218  [0.047030162, -0.03762929, -0.055747997, 0.016...   
5219  [0.047030162, -0.03762929, -0.055747997, 0.016...   
5220  [0.047030162, -0.03762929, -0.055747997, 0.016...   

                                        Terms_embedding  \
0     [0.06673001, -0.034514982, -0.049483243, -0.02...   
1     [0.06673001, -0.034514982, -0.049483243, -0.02...   
2     [0.06673001, -0.034514982, -0.04948324

In [18]:
df['Keywords'].iloc[0].type()

AttributeError: 'list' object has no attribute 'type'

In [26]:
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np
import pandas as pd

# 벡터 스택: (n_samples, embedding_dim)
embedding_matrix = np.vstack(df['Embedding_content_embedding'].values)

# cosine similarity 전체 행렬
similarity_matrix = cosine_similarity(embedding_matrix)

recommendations = []

for idx, row in df.iterrows():
    current_domain = row['Domain']
    current_division = row['division']
    current_q_number = row['Question_Number']

    # 비교 대상: 같은 Domain이면서 division이 'Description'인 행만 대상
    candidate_mask = (df['Domain'] == current_domain) & (df['division'] == 'Description')
    candidate_indices = df[candidate_mask].index.tolist()

    # 자기 자신은 제외
    candidate_indices = [i for i in candidate_indices if i != idx]

    # 현재 행이 어떤 벡터와 비교할지 유사도 추출
    sim_scores = similarity_matrix[idx][candidate_indices]

    # 추천 개수 설정
    top_k = 5 if current_division == 'Description' else 3

    # 유사도 기준 상위 K개 추천
    if len(sim_scores) > 0:
        top_indices = np.argsort(sim_scores)[-top_k:][::-1]
        recommended_indices = [candidate_indices[i] for i in top_indices]
        recommended_q_numbers = df.loc[recommended_indices, 'Question_Number'].tolist()
    else:
        recommended_q_numbers = []

    recommendations.append(recommended_q_numbers)

# 결과 저장
df['Recommend_question'] = recommendations


In [28]:
df.to_csv("./aws_embedding.csv")

In [30]:
print(len(data))

1017


In [29]:
with open("/Users/twj/Desktop/aws_project/aws_saa_test_backend/data_generate/data_json변환/questions_fixed_complete.json", "r") as f:
    data = json.load(f)
data

[{'Question_Number': 'Q1',
  'Question_Description': '한 회사가 여러 대륙의 도시들에서 온도, 습도, 대기압 데이터를 수집하고 있습니다. 각 사이트에서 매일 수집하는 평균 데이터 볼륨은 500GB입니다. 각 사이트는 고속 인터넷 연결을 보유하고 있습니다. 회사는 이러한 모든 글로벌 사이트의 데이터를 단일 Amazon S3 버킷에 가능한 한 빠르게 집계하려고 합니다. 솔루션은 운영 복잡성을 최소화해야 합니다. 이러한 요구사항을 충족하는 솔루션은 무엇입니까?',
  'Answer': 'A',
  'Link': 'https://www.examtopics.com/discussions/amazon/view/84973-exam-aws-certified-solut',
  'AnswerDescription': '이 문제는 전 세계 지점에서 발생하는 대규모 데이터를 단일 Amazon S3 버킷으로 빠르고 간편하게 업로드하는 방법을 묻고 있습니다. S3 Transfer Acceleration을 사용하면 네트워크 지연을 줄이고, Multipart Upload로 대용량 데이터를 병렬 전송하여 업로드 속도를 높이는 최적의 해법을 구현할 수 있습니다.',
  'Domain': '고성능 아키텍처 설계',
  'Tasks': ['3.1', '3.4'],
  'Keywords': ['글로벌 사이트',
   '500GB',
   '고속 인터넷',
   '운영 복잡성',
   'Amazon S3',
   'S3 Transfer Acceleration',
   'Multipart Upload'],
  'Terms': ['S3 Transfer Acceleration',
   'Multipart Upload',
   'S3 Cross-Region Replication',
   'AWS Snowball Edge',
   'Amazon EBS',
   'EBS Snapshot'],
  'SelectA': '대상 S3 버킷에서 S3 Transfer Acceler

In [31]:
df

index       Domain Question_Number  \
0         0  고성능 아키텍처 설계              Q1   
1         0  고성능 아키텍처 설계              Q1   
2         0  고성능 아키텍처 설계              Q1   
3         0  고성능 아키텍처 설계              Q1   
4         0  고성능 아키텍처 설계              Q1   
...     ...          ...             ...   
5216   1016   보안 아키텍처 설계           Q1019   
5217   1016   보안 아키텍처 설계           Q1019   
5218   1016   보안 아키텍처 설계           Q1019   
5219   1016   보안 아키텍처 설계           Q1019   
5220   1016   보안 아키텍처 설계           Q1019   

                                               Keywords  \
0     글로벌 사이트 500GB 고속 인터넷 운영 복잡성 Amazon S3 S3 Trans...   
1     글로벌 사이트 500GB 고속 인터넷 운영 복잡성 Amazon S3 S3 Trans...   
2     글로벌 사이트 500GB 고속 인터넷 운영 복잡성 Amazon S3 S3 Trans...   
3     글로벌 사이트 500GB 고속 인터넷 운영 복잡성 Amazon S3 S3 Trans...   
4     글로벌 사이트 500GB 고속 인터넷 운영 복잡성 Amazon S3 S3 Trans...   
...                                                 ...   
5216  Amazon API Gateway HTTP API 회사 내부 네트워크 IP 주소 제...   
5217  Amazon API Gateway HTTP API 회사 내부 네트워크 IP 주소 제...   
5218  Amazon API Gateway HTTP API 회사 내부 네트워크 IP 주소 제...   
5219  Amazon API Gateway HTTP API 회사 내부 네트워크 IP 주소 제...   
5220  Amazon API Gateway HTTP API 회사 내부 네트워크 IP 주소 제...   

                                                  Terms     division  \
0     S3 Transfer Acceleration Multipart Upload S3 C...  Description   
1     S3 Transfer Acceleration Multipart Upload S3 C...    Selection   
2     S3 Transfer Acceleration Multipart Upload S3 C...    Selection   
3     S3 Transfer Acceleration Multipart Upload S3 C...    Selection   
4     S3 Transfer Acceleration Multipart Upload S3 C...    Selection   
...                                                 ...          ...   
5216  Amazon API Gateway Resource Policy Security Gr...  Description   
5217  Amazon API Gateway Resource Policy Security Gr...    Selection   
5218  Amazon API Gateway Resource Policy Security Gr...    Selection   
5219  Amazon API Gateway Resource Policy Security Gr...    Selection   
5220  Amazon API Gateway Resource Policy Security Gr...    Selection   

                   mapping                                  Embedding_content  \
0     Question_Description  한 회사가 여러 대륙의 도시들에서 온도, 습도, 대기압 데이터를 수집하고 있습니다....   
1                  SelectA  대상 S3 버킷에서 S3 Transfer Acceleration을 활성화하고, Mu...   
2                  SelectB  가장 가까운 리전의 S3 버킷에 데이터를 업로드하고, S3 Cross-Region ...   
3                  SelectC  AWS Snowball Edge Storage Optimized 디바이스를 매일 예...   
4                  SelectD  가장 가까운 리전의 Amazon EC2 인스턴스에 데이터를 업로드하고, Amazon...   
...                    ...                                                ...   
5216  Question_Description  한 회사가 AWS Cloud에서 애플리케이션을 개발 중입니다. 애플리케이션의 HTT...   
5217               SelectA  API Gateway에 Private Integration을 설정하고 사전에 정의된...   
5218               SelectB  API에 Resource Policy를 생성하여 명시적으로 허용되지 않은 모든 IP...   
5219               SelectC  API를 사설 서브넷에 직접 배포하고, Network ACL을 생성하여 특정 IP ...   
5220               SelectD  API Gateway에 연결된 Security Group을 수정하여 신뢰할 수 있는...   

                                     keywords_embedding  \
0     [0.082221694, -0.036399595, -0.054603774, -0.0...   
1     [0.082221694, -0.036399595, -0.054603774, -0.0...   
2     [0.082221694, -0.036399595, -0.054603774, -0.0...   
3     [0.082221694, -0.036399595, -0.054603774, -0.0...   
4     [0.082221694, -0.036399595, -0.054603774, -0.0...   
...                                                 ...   
5216  [0.047030162, -0.03762929, -0.055747997, 0.016...   
5217  [0.047030162, -0.03762929, -0.055747997, 0.016...   
5218  [0.047030162, -0.03762929, -0.055747997, 0.016...   
5219  [0.047030162, -0.03762929, -0.055747997, 0.016...   
5220  [0.047030162, -0.03762929, -0.055747997, 0.016...   

                                        Terms_embedding  \
0     [0.06673001, -0.034514982, -0.049483243, -0.02...   
1     [0.06673001, -0.034514982, -0.049483243, -0.02...   
2     [0.06673001, -0.034514982, -0.04948324

In [37]:
new_json = [{} for i in range(1017)]
result = []
for i, row in df.iterrows():
    # original_data = data[row['index']]
    # if row['division'] == 'Description':
    new_json[row['index']][row['mapping']+'_recommedations'] = row['Recommend_question']
new_json
for i in range(1017):
    result.append(data[i] | new_json[i])
result

[{'Question_Number': 'Q1',
  'Question_Description': '한 회사가 여러 대륙의 도시들에서 온도, 습도, 대기압 데이터를 수집하고 있습니다. 각 사이트에서 매일 수집하는 평균 데이터 볼륨은 500GB입니다. 각 사이트는 고속 인터넷 연결을 보유하고 있습니다. 회사는 이러한 모든 글로벌 사이트의 데이터를 단일 Amazon S3 버킷에 가능한 한 빠르게 집계하려고 합니다. 솔루션은 운영 복잡성을 최소화해야 합니다. 이러한 요구사항을 충족하는 솔루션은 무엇입니까?',
  'Answer': 'A',
  'Link': 'https://www.examtopics.com/discussions/amazon/view/84973-exam-aws-certified-solut',
  'AnswerDescription': '이 문제는 전 세계 지점에서 발생하는 대규모 데이터를 단일 Amazon S3 버킷으로 빠르고 간편하게 업로드하는 방법을 묻고 있습니다. S3 Transfer Acceleration을 사용하면 네트워크 지연을 줄이고, Multipart Upload로 대용량 데이터를 병렬 전송하여 업로드 속도를 높이는 최적의 해법을 구현할 수 있습니다.',
  'Domain': '고성능 아키텍처 설계',
  'Tasks': ['3.1', '3.4'],
  'Keywords': ['글로벌 사이트',
   '500GB',
   '고속 인터넷',
   '운영 복잡성',
   'Amazon S3',
   'S3 Transfer Acceleration',
   'Multipart Upload'],
  'Terms': ['S3 Transfer Acceleration',
   'Multipart Upload',
   'S3 Cross-Region Replication',
   'AWS Snowball Edge',
   'Amazon EBS',
   'EBS Snapshot'],
  'SelectA': '대상 S3 버킷에서 S3 Transfer Acceler

In [40]:
with open("./questions_fixed_complete.json", "w", encoding="utf-8") as f:
    json.dump(result,f,ensure_ascii=False, indent=2)

In [25]:
df.to_csv("./aws_embedding.csv")